In [1]:
import numpy as np
import IPython.display as idisplay
import matplotlib.pyplot as plt
from scipy.io.wavfile import read, write

In [2]:
if True:
    sample_rate, waveform = read("fastcar.wav")
    waveform = np.transpose(waveform)
else:
    sample_rate = 44100
    waveform = np.sin(np.linspace(0,6,sample_rate*6) * 2 * np.pi * 440) * 512 # 440 hz sine wave
    waveform = np.reshape(waveform, (2, -1))
channels, og_num_samples = waveform.shape
print(waveform.shape, waveform.dtype, sample_rate)
print(f"Input range: {np.min(waveform)} - {np.max(waveform)}")
idisplay.display(idisplay.Audio(waveform, rate=sample_rate))
# plt.plot(waveform[0, 100000:105000])

(2, 882000) int16 44100
Input range: -21131 - 17205


In [17]:
def alvin_and_the_chipmunks_in_hell(input_waveform: np.ndarray, pitch_up_factor: float, window_size=1000) -> np.ndarray:
    input_num_samples = input_waveform.shape[1]
    analysis_hop_length = int(window_size / pitch_up_factor)
    synthesis_hop_length = window_size
    
    output_num_samples = int(input_num_samples / analysis_hop_length) * synthesis_hop_length + input_num_samples % analysis_hop_length
    
    print("total length stretch:",output_num_samples/input_num_samples)
    
    output_waveform = np.zeros((channels, output_num_samples), dtype=np.int16)
    output_location = 0
    # print("input num samples:",input_num_samples)
    # print("analysis hop length:",analysis_hop_length)
    # print("output_waveform shape:",output_waveform.shape)
    
    for i in range(0, input_num_samples, analysis_hop_length):
        this_window_size = min(i+window_size, input_num_samples) - i
        
        window = input_waveform[:, i:i+this_window_size]
        # print(f'window size of {this_window_size}, sampled from input_waveform[{i}:{i+this_window_size}] being written in output_waveform[{output_location}:{output_location+this_window_size}]')
        output_waveform[:, output_location:output_location+this_window_size] = window
        output_location += synthesis_hop_length

    return output_waveform

chipmunk_pitch_factor = 0.5
chipmunk_hell = alvin_and_the_chipmunks_in_hell(waveform, chipmunk_pitch_factor, 1000)
idisplay.display(idisplay.Audio(chipmunk_hell, rate=sample_rate*chipmunk_pitch_factor))
print(f"Output range: {np.min(chipmunk_hell)} - {np.max(chipmunk_hell)}")
# plt.plot(output_waveform[0, 100000*pitch_up_factor:105000*pitch_up_factor])
# plt.plot(output_waveform[0, 1700000:1764000])

total length stretch: 0.5


Output range: -21131 - 17191


- 2, 1000 is a "good" pitchup
- 2, 100 creates some fun noise - seems like decreasing window size increases noise
- 0.5, 10000 is crazy and trippy and makes me feel like there's something wrong with my head
- higher pitchups than 2 just sound goofy (think that's normal?)

In [ ]:
def OLA(input_waveform: np.ndarray, pitch_up_factor:float, window_size=1000):
    input_num_samples = input_waveform.shape[1]
    overlap = 100
    window_function = np.hanning(window_size)
    
    analysis_hop_length = int((window_size - overlap) / pitch_up_factor)
    synthesis_hop_length = window_size - overlap
    
    output_num_samples = int(input_num_samples / analysis_hop_length) * synthesis_hop_length + input_num_samples % analysis_hop_length
    print("total length stretch:",output_num_samples/input_num_samples)




In [14]:
import librosa
print(np.max(output_waveform, axis=1), np.argmax(output_waveform, axis=1))
to_save = librosa.resample(output_waveform, orig_sr=sample_rate*pitch_up_factor, target_sr=44100)
# to_save = output_waveform
print(np.max(waveform, axis=1), np.max(to_save), np.min(to_save))
print(to_save.shape)
write("output.wav", 44100, to_save.astype(np.int16).transpose())

[2261634.50980392              nan] [1759500 1759500]


ParameterError: Audio buffer is not finite everywhere